In [34]:
import plotly.express as px
import pyspark

In [35]:
spark = pyspark.sql.SparkSession.builder.appName("Stars").getOrCreate()

In [36]:
df = spark.read.csv('cleaned_crime.csv', header=True, inferSchema=True)

In [4]:
df.printSchema()


root
 |-- OFFENSE_TYPE_ID: string (nullable = true)
 |-- OFFENSE_CATEGORY_ID: string (nullable = true)
 |-- FIRST_OCCURRENCE_DATE: string (nullable = true)
 |-- REPORTED_DATE: string (nullable = true)
 |-- GEO_X: double (nullable = true)
 |-- GEO_Y: double (nullable = true)
 |-- GEO_LON: double (nullable = true)
 |-- GEO_LAT: double (nullable = true)
 |-- NEIGHBORHOOD_ID: string (nullable = true)
 |-- IS_CRIME: integer (nullable = true)
 |-- IS_TRAFFIC: integer (nullable = true)
 |-- VICTIM_COUNT: integer (nullable = true)



In [39]:
df.select("REPORTED_DATE").show(10)

+--------------------+
|       REPORTED_DATE|
+--------------------+
|6/27/2017 7:01:00 PM|
|5/26/2017 11:04:0...|
|6/27/2017 5:50:00 PM|
|5/26/2017 10:21:0...|
| 7/7/2017 9:48:00 PM|
|5/16/2017 1:04:00 AM|
|7/7/2017 11:53:00 PM|
|10/7/2017 1:10:00 AM|
|9/3/2017 11:25:00 AM|
|8/12/2017 7:05:00 PM|
+--------------------+
only showing top 10 rows



In [28]:
from pyspark.sql.functions import *

In [45]:
spark.sql("set spark.sql.legacy.timeParserPolicy=LEGACY")
# convert FIRST_OCCURRENCE_DATE to a timestamp in format MM/dd/yyyy hh:mm:ss a
df = df.withColumn("FIRST_OCCURRENCE_DATE", to_timestamp("FIRST_OCCURRENCE_DATE", "MM/dd/yyyy hh:mm:ss a"))
df = df.withColumn("REPORTED_DATE", to_timestamp("REPORTED_DATE", "MM/dd/yyyy hh:mm:ss a"))

In [46]:
df.limit(2).toPandas().head()


/opt/homebrew/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:248: FutureWarning:

Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead

/opt/homebrew/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:248: FutureWarning:

Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead



OFFENSE_TYPE_ID OFFENSE_CATEGORY_ID FIRST_OCCURRENCE_DATE  \
0  criminal-mischief-other     public-disorder   2017-06-25 20:40:00   
1  criminal-mischief-other     public-disorder   2017-05-26 19:00:00   

        REPORTED_DATE      GEO_X      GEO_Y     GEO_LON    GEO_LAT  \
0 2017-06-27 19:01:00  3133773.0  1702660.0 -105.024167  39.761646   
1 2017-05-26 23:04:00  3185904.0  1709037.0 -104.838576  39.778256   

  NEIGHBORHOOD_ID  IS_CRIME  IS_TRAFFIC  VICTIM_COUNT  
0        highland         1           0             1  
1       montbello         1           0             1

In [48]:
# select GEO_LON an GEO_LAT columns for the first 1000 rows
geo_df = (df.sample(False,0.01,seed=42).select('GEO_LON', 'GEO_LAT','OFFENSE_CATEGORY_ID','VICTIM_COUNT','FIRST_OCCURRENCE_DATE')).toPandas()

/opt/homebrew/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:248: FutureWarning:

Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead



In [16]:
from pyspark.sql.functions import *

In [ ]:
# how to select all from a pyspark dataframe


In [24]:
(
    df
        .select('*')
        .filter(col('NEIGHBORHOOD_ID') == "highland").filter(col('VICTIM_COUNT') > 0)
        .show(10)
)

+--------------------+-------------------+---------------------+--------------------+---------+---------+------------+----------+---------------+--------+----------+------------+
|     OFFENSE_TYPE_ID|OFFENSE_CATEGORY_ID|FIRST_OCCURRENCE_DATE|       REPORTED_DATE|    GEO_X|    GEO_Y|     GEO_LON|   GEO_LAT|NEIGHBORHOOD_ID|IS_CRIME|IS_TRAFFIC|VICTIM_COUNT|
+--------------------+-------------------+---------------------+--------------------+---------+---------+------------+----------+---------------+--------+----------+------------+
|criminal-mischief...|    public-disorder| 6/25/2017 8:40:00 PM|6/27/2017 7:01:00 PM|3133773.0|1702660.0|-105.0241665|39.7616457|       highland|       1|         0|           1|
|criminal-mischief...|    public-disorder| 6/10/2017 3:30:00 AM|6/10/2017 3:14:00 PM|3137479.0|1702852.0|-105.0109808|39.7621188|       highland|       1|         0|           1|
|criminal-mischief...|    public-disorder| 6/29/2017 9:47:00 PM|6/29/2017 9:47:00 PM|3138151.0|1700947.0|

In [47]:
df.printSchema()

root
 |-- OFFENSE_TYPE_ID: string (nullable = true)
 |-- OFFENSE_CATEGORY_ID: string (nullable = true)
 |-- FIRST_OCCURRENCE_DATE: timestamp (nullable = true)
 |-- REPORTED_DATE: timestamp (nullable = true)
 |-- GEO_X: double (nullable = true)
 |-- GEO_Y: double (nullable = true)
 |-- GEO_LON: double (nullable = true)
 |-- GEO_LAT: double (nullable = true)
 |-- NEIGHBORHOOD_ID: string (nullable = true)
 |-- IS_CRIME: integer (nullable = true)
 |-- IS_TRAFFIC: integer (nullable = true)
 |-- VICTIM_COUNT: integer (nullable = true)



In [49]:
# scatter geo for Denver satellite view

fig = px.scatter_mapbox(geo_df, lat=geo_df.GEO_LAT, lon=geo_df.GEO_LON, zoom=10, height=300,hover_data=['OFFENSE_CATEGORY_ID'],color='VICTIM_COUNT',
                        animation_frame="FIRST_OCCURRENCE_DATE")
fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "United States Geological Survey",
            "source": [
                "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            ]
        }
      ])

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

KeyError: Timestamp('2017-01-10 22:45:00')

In [25]:
crime_types = df.select('OFFENSE_CATEGORY_ID').distinct().toPandas()['OFFENSE_CATEGORY_ID'].tolist()

In [26]:
crime_types 

['sexual-assault',
 'burglary',
 'murder',
 'aggravated-assault',
 'auto-theft',
 'theft-from-motor-vehicle',
 'other-crimes-against-persons',
 'all-other-crimes',
 'arson',
 'public-disorder',
 'robbery',
 'drug-alcohol',
 'larceny',
 'white-collar-crime']

In [4]:
df.printSchema()

root
 |-- OFFENSE_TYPE_ID: string (nullable = true)
 |-- OFFENSE_CATEGORY_ID: string (nullable = true)
 |-- FIRST_OCCURRENCE_DATE: timestamp (nullable = true)
 |-- REPORTED_DATE: timestamp (nullable = true)
 |-- GEO_X: double (nullable = true)
 |-- GEO_Y: double (nullable = true)
 |-- GEO_LON: double (nullable = true)
 |-- GEO_LAT: double (nullable = true)
 |-- NEIGHBORHOOD_ID: string (nullable = true)
 |-- IS_CRIME: integer (nullable = true)
 |-- IS_TRAFFIC: integer (nullable = true)
 |-- VICTIM_COUNT: integer (nullable = true)



In [5]:
from pyspark.sql.functions import *

In [34]:
# group by the day of the timestamp FIRST_OCCURRENCE_DATE
df_count_day = (df.withColumn("day", dayofmonth("FIRST_OCCURRENCE_DATE"))
    .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
    .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
    .select("day","month","year")
    .groupBy("day", "month", "year")
    .agg(count("*").alias("count"))
    
    
)

In [39]:
# concatenate year date month in one column as an a date type
df_count_day = df_count_day.withColumn("date", concat(col("year"), lit("-"), col("month"), lit("-"), col("day"))).withColumn("date", to_date("date", "yyyy-M-d"))
df_count_day = df_count_day.drop("day", "month", "year")


In [40]:
df_count_day.show(10)

+-----+----------+
|count|      date|
+-----+----------+
|  156|2017-06-19|
|  186|2017-10-05|
|  164|2017-04-13|
|  191|2017-06-15|
|  169|2017-12-19|
|  216|2017-06-16|
|  182|2017-05-09|
|  209|2017-09-22|
|  115|2017-11-23|
|  142|2017-04-29|
+-----+----------+
only showing top 10 rows



In [41]:
df_count_day_pandas = df_count_day.toPandas()

In [43]:
# plot a line chart with date the x axis and count on the y axis



In [44]:
def get_pandas_by_day(df):
    df_count_day = (df.withColumn("day", dayofmonth("FIRST_OCCURRENCE_DATE"))
    .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
    .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
    .select("day","month","year")
    .groupBy("day", "month", "year")
    .agg(count("*").alias("count"))
    )
    df_count_day = df_count_day.withColumn("date", concat(col("year"), lit("-"), col("month"), lit("-"), col("day"))).withColumn("date", to_date("date", "yyyy-M-d"))
    df_count_day = df_count_day.drop("day", "month", "year")
    return df_count_day.toPandas()


In [65]:
def get_pandas_by_month(df):
    df_count_month = (
        df
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .select("month","year")
            .groupBy("month", "year")
            .agg(count("*").alias("count"))
    )
    df_count_month = df_count_month.withColumn("date", concat(col("year"), lit("-"), col("month"))).withColumn("date", date_format("date", "yyyy-M"))
    df_count_month = df_count_month.drop("month", "year")
    return df_count_month.toPandas()


In [52]:
df_count_month = (
        df
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .select("month","year")
            .groupBy("month", "year")
            .agg(count("*").alias("count"))
    )

In [66]:
get_pandas_by_month(df).head()

count    date
0   4753  2017-1
1   5227  2017-3
2   5667  2017-6
3     53    None
4   5717  2017-7

In [70]:
fig = px.scatter(get_pandas_by_month(df), x="date", y="count", color="count", hover_data=['count'])
fig.show()

In [71]:
def get_pandas_by_year(df):
    df_count_year = (
        df
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .select("year")
            .groupBy("year")
            .agg(count("*").alias("count"))
    )
    df_count_year = df_count_year.withColumn("date", concat(col("year"))).withColumn("date", date_format("date", "yyyy"))
    df_count_year = df_count_year.drop("year")
    return df_count_year.toPandas()

In [72]:
fig = px.scatter(get_pandas_by_year(df), x="date", y="count", color="count", hover_data=['count'])
fig.show()

In [127]:


def get_pandas_filtered(df,neighborhood,crime_type):
    if(neighborhood == 'All'):
        df_cleaned = df
    else:
        df_cleaned = df.filter(df["NEIGHBORHOOD_ID"]==neighborhood)
    if(crime_type == 'All'):
        df_cleaned = df_cleaned
    else:
        df_cleaned = df_cleaned.filter(df_cleaned["OFFENSE_CATEGORY_ID"]==crime_type)
    geo_df = (df_cleaned.sample(False,0.1,seed=42).select('GEO_LON', 'GEO_LAT','OFFENSE_CATEGORY_ID','VICTIM_COUNT','NEIGHBORHOOD_ID')).toPandas()
    return geo_df

In [128]:
def getMap(df,neighborhood,crime_type):
    geo_df = get_pandas_filtered(df,neighborhood,crime_type)
    fig = px.scatter_mapbox(geo_df, lat=geo_df.GEO_LAT, lon=geo_df.GEO_LON, zoom=10, height=300,hover_data=['NEIGHBORHOOD_ID','OFFENSE_CATEGORY_ID'],color='VICTIM_COUNT')
    fig.update_layout(
        mapbox_style="white-bg",
        mapbox_layers=[
            {
                "below": 'traces',
                "sourcetype": "raster",
                "sourceattribution": "United States Geological Survey",
                "source": [
                    "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
                ]
            }
        ])

    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
    return fig

In [129]:
fig = getMap(df,'All','All')
fig.show()


In [79]:
def get_pandas_num_crimes_based_on_neighborhood(df):
    df_count_neighborhood = (
        df
            .select("NEIGHBORHOOD_ID")
            .groupBy("NEIGHBORHOOD_ID")
            .agg(count("*").alias("count"))
    )
    return df_count_neighborhood.toPandas()

def get_pandas_mean_num_crimes_based_on_neighborhood(df):
    df_count_neighborhood = (
        df
            .select("NEIGHBORHOOD_ID")
            .groupBy("NEIGHBORHOOD_ID")
            .agg(mean("*").alias("mean"))
    )
    return df_count_neighborhood.toPandas()

In [82]:
# bar plot of the number of crimes based on neighborhood
fig = px.bar(get_pandas_num_crimes_based_on_neighborhood(df), x="NEIGHBORHOOD_ID", y="count", color="count", hover_data=['count'])
fig.show()

In [81]:
# bar plot of the mean of crimes based on neighborhood
fig = px.bar(get_pandas_mean_num_crimes_based_on_neighborhood(df), x="NEIGHBORHOOD_ID", y="mean", color="mean", hover_data=['mean'])


AnalysisException: Invalid usage of '*' in expression 'avg'

In [32]:
from pyspark.sql.types import *
def get_pandas_timeline(df):
    # get day from FIRST_OCCURRENCE_DATE, aggregate by day and count all rows
    df_count_day = (
        df
            .withColumn("day", dayofmonth("FIRST_OCCURRENCE_DATE"))
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .groupBy("day", "month", "year")
            
            
    )
    df_count_day = df_count_day.withColumn("date", concat(col("year"), lit("-"), col("month"), lit("-"), col("day"))).withColumn("date", to_date("date", "yyyy-M-d"))
    df_count_day = df_count_day.drop("day", "month", "year")
    return df_count_day.toPandas()

In [8]:
from pyspark.sql.functions import *

In [5]:
def get_map_timeline(df):
    df_pandas = get_pandas_timeline(df)

    print(df_pandas.shape)

    # a scatter_geo with animation frame based on REPORTED_DATE
    fig = px.scatter_geo(df_pandas, lat="GEO_LAT", lon="GEO_LON", scope='usa', animation_frame="date")



In [33]:
fig = get_map_timeline(df)
fig.show()

AttributeError: 'GroupedData' object has no attribute 'withColumn'

In [53]:
df_count_day = (
        df
            .withColumn("day", dayofmonth("FIRST_OCCURRENCE_DATE"))
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .groupBy("day", "month", "year")
            .agg(mean("GEO_LAT").alias("GEO_LAT"), mean("GEO_LON").alias("GEO_LON"))
    )
df_count_day = df_count_day.withColumn("date_month",concat(col("year"), lit("-"), col("month"))).withColumn("date_month", to_date("date_month", "yyyy-M"))
df_count_day = df_count_day.withColumn("date", concat(col("year"), lit("-"), col("month"), lit("-"), col("day"))).withColumn("date", to_date("date", "yyyy-M-d"))
df_count_day = df_count_day.drop("day", "month", "year")

In [54]:
df_count_day.show()

+------------------+-------------------+----------+----------+
|           GEO_LAT|            GEO_LON|date_month|      date|
+------------------+-------------------+----------+----------+
| 39.66300703355381|-105.11099542502645|2017-06-01|2017-06-19|
| 39.67326514711237| -105.0710946412045|2017-10-01|2017-10-05|
| 39.67359550193414|-105.08856016190282|2017-04-01|2017-04-13|
|39.730600061346586|-104.97142906676471|2017-06-01|2017-06-15|
| 39.65062165776864|-105.14603884712452|2017-12-01|2017-12-19|
|39.476325169100896|-104.62843137050044|2017-06-01|2017-06-16|
| 39.64398632117745|-105.13852993400005|2017-05-01|2017-05-09|
| 39.70688333401244|-105.02750662572267|2017-09-01|2017-09-22|
|39.680863986633874|-105.05037623012215|2017-11-01|2017-11-23|
| 39.65513167124788|-105.11282228346525|2017-04-01|2017-04-29|
| 39.65326642402345|-105.12640209783693|2017-02-01|2017-02-15|
| 39.73144083707408|-104.97020209209647|2017-04-01|2017-04-18|
| 39.68532047441508|-105.06722498028158|2017-08-01|2017

In [55]:
df_pandas = df_count_day.toPandas()

In [57]:
fig = px.scatter_geo(df_pandas, lat="GEO_LAT", lon="GEO_LON", scope='usa', animation_frame="date_month")
fig.show()

In [82]:
df_animated_neighborhood = (
        df
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .groupBy("month", "year", "NEIGHBORHOOD_ID")
            .agg(count("*").alias("count_crimes"))
            .orderBy("NEIGHBORHOOD_ID")
    )
df_animated_neighborhood = df_animated_neighborhood.withColumn("date_month",concat(col("year"), lit("-"), col("month"))).withColumn("date_month", to_date("date_month", "yyyy-M"))
df_animated_neighborhood = df_animated_neighborhood.drop("month", "year")
df_animated_neighborhood.show()


+---------------+------------+----------+
|NEIGHBORHOOD_ID|count_crimes|date_month|
+---------------+------------+----------+
|              1|          87|2019-11-01|
|              1|          65|2017-04-01|
|              1|          71|2019-05-01|
|              1|          82|2018-09-01|
|              1|          86|2019-08-01|
|              1|          48|2017-12-01|
|              1|          69|2021-03-01|
|              1|          47|2017-11-01|
|              1|          58|2018-12-01|
|              1|          69|2019-09-01|
|              1|          86|2020-08-01|
|              1|         142|2022-07-01|
|              1|          60|2020-01-01|
|              1|          69|2019-12-01|
|              1|         173|2022-05-01|
|              1|          64|2020-12-01|
|              1|          64|2020-02-01|
|              1|          85|2017-06-01|
|              1|          37|2018-11-01|
|              1|          63|2019-04-01|
+---------------+------------+----

In [83]:
df_animated_neighborhood_pd = df_animated_neighborhood.toPandas()

In [85]:
# animation frame based on date_month, bar plot
# color based on count_crimes
fig = px.bar(df_animated_neighborhood_pd, x="count_crimes", y="NEIGHBORHOOD_ID", color="count_crimes", animation_frame="date_month", hover_data=['count_crimes'])
# make the animation slower
fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 1000
# make the labels to not change during the animation


# set graph dimension
fig.update_layout(width=700, height=700)
fig.show()

In [87]:
df.printSchema()

root
 |-- OFFENSE_TYPE_ID: string (nullable = true)
 |-- OFFENSE_CATEGORY_ID: string (nullable = true)
 |-- FIRST_OCCURRENCE_DATE: timestamp (nullable = true)
 |-- REPORTED_DATE: timestamp (nullable = true)
 |-- GEO_X: double (nullable = true)
 |-- GEO_Y: double (nullable = true)
 |-- GEO_LON: double (nullable = true)
 |-- GEO_LAT: double (nullable = true)
 |-- NEIGHBORHOOD_ID: string (nullable = true)
 |-- IS_CRIME: integer (nullable = true)
 |-- IS_TRAFFIC: integer (nullable = true)
 |-- VICTIM_COUNT: integer (nullable = true)



In [91]:
(
        df
            .withColumn("month", month("FIRST_OCCURRENCE_DATE"))
            .withColumn("year", year("FIRST_OCCURRENCE_DATE"))
            .groupBy("month", "year")
            .agg(sum("VICTIM_COUNT").alias("count"))
            .show()
 )

+-----+----+-----+
|month|year|count|
+-----+----+-----+
|    1|2017| 4826|
|    3|2017| 5313|
|    6|2017| 5772|
| null|null|   55|
|    7|2017| 5823|
|    8|2017| 6242|
|   11|2017| 5105|
|    9|2017| 5702|
|    2|2017| 4581|
|    4|2017| 5219|
|   12|2017| 4870|
|    5|2017| 5619|
|   10|2017| 5533|
|    7|2018| 5950|
|   11|2021| 6424|
|    5|2022| 7544|
|    6|2018| 5598|
|    6|2019| 5714|
|   12|2020| 6344|
|    3|2018| 5179|
+-----+----+-----+
only showing top 20 rows



In [96]:
df.filter(col("VICTIM_COUNT") ==3).count()

791

In [99]:
(
        df  
            
            .groupBy("VICTIM_COUNT")
            
            .agg(count("*").alias("num_crimes"))
            .select(col("VICTIM_COUNT").alias("num_victims"), "num_crimes")
    ).show(10)

+------------+----------+
|VICTIM_COUNT|num_crimes|
+------------+----------+
|           1|    394224|
|           6|        70|
|           3|       791|
|           5|       156|
|           9|        14|
|           4|       269|
|           8|        29|
|           7|        46|
|          10|         6|
|          32|         1|
+------------+----------+
only showing top 10 rows

